In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from typing import TypeAlias
from IPython.display import HTML
%matplotlib inline

Number: TypeAlias = int | float

def number(cin: str) -> Number | None:
    """
    La función number retorna un dato de tipo Number,
    recibe una cadena como parámetro y la función en base a lo recibido,
    retorna un flotante, un entero o en su defecto, retorna None
    """

    result: Number
    if '.' in cin:
        try:
            result = float(cin)
        except ValueError:
            return None

        return result

    try:
        result = int(cin)
    except ValueError:
        return None
    
    return result

def valid(msg: str, value_min: Number | None = None, value_max: Number | None = None, positive: bool = True) -> Number | None:
    """"
    Valida que la entrada de un número esté correcta teniendo en cuenta criterios
    como que tenga que ser un número positivo, el mínimo valor que pueda tomar o
    el máximo valor

    - param msg: str. Es el mensaje que imprime el programa para pedir la entrada
    - param value_min: Number. Es el mínimo valor que puede tomar la entrada (sin incluirlo),
    además, cuando se le es dado el valor None (viene por defecto), no lo toma en cuenta
    - param value_max: Number. Funciona de manera analoga a value_min, con la diferencia
    que se refiere al valor máximo que puede tomar el programa
    - param positive: bool. Quiere decirle al programa que la entrada del número que se desea
    tiene que ser mayor o igual a 0, por defecto está tomado como True

    La función retorna un dato de tipo Number después de haber válidado la entrada
    previamente. En caso de que los parámetros value_min y value_max no estén
    bien planteado (value_min > value_max), la función retorna None
    """

    result: Number | None = None

    if value_min is None and value_max is None:
        while result is None or (result < 0 and positive):
            result = number(input(msg))

            if result is None:
                print('El valor tiene que ser númerico')
                continue

            if result < 0 and positive:
                print('El valor tiene que ser mayor que 0')
        
        return result

    if value_min is None and value_max is not None:
        while result is None or (result < 0 and positive) or result >= value_max:
            result = number(input(msg))

            if result is None:
                print('El valor tiene que ser númerico')
                continue

            if result < 0 and positive:
                print('El valor tiene que ser mayor que 0')
            if result >= value_max:
                print(f'El valor tiene que ser menor que {value_max}')
        
        return result

    if value_max is None and value_min is not None:
        while result is None or (result < 0 and positive) or result <= value_min:
            result = number(input(msg))

            if result is None:
                print('El valor tiene que ser númerico')
                continue

            if result < 0 and positive:
                print('El valor tiene que ser mayor que 0')
            if result <= value_min:
                print(f'El valor tiene que ser mayor que {value_min}')

        return result
    
    if value_min > value_max:
        return result # Retorna None
    
    if value_min == value_max:
        return value_min

    while result is None or (result < 0 and positive) or result <= value_min or result >= value_max:
        result = number(input(msg))

        if result is None:
            print('El valor tiene que ser númerico')
            continue

        if result < 0 and positive:
            print('El valor tiene que ser mayor que 0')
        else:
            if result <= value_min:
                print(f'El valor tiene que ser mayor que {value_min}')
            if result >= value_max:
                print(f'El valor tiene que ser menor que {value_max}')

    return result

In [8]:
force: Number = valid('Rope tension [N]: ', value_min=0)
mass: Number = valid('Rope mass [Kg]: ', value_min=0)
length: Number = valid('Rope length [m]: ', value_min=0)

freq: Number = valid('Frequency [Hz]: ', value_min=0)
amplitude: Number = valid('Amplitude [m]: ', value_min=0)

x0: Number = valid('Initial position [m]: ', positive=False)
v0: Number = valid('Initial velocity [m/s]: ', positive=False)

t: Number = valid('Wave observation time [s]: ') + 1

print('\nUser input')
print(f'Rope tension: {force = } N')
print(f'Rope mass: {mass = } Kg')
print(f'Rope length: {length = } m')
print(f'Frequency: {freq = } Hz')
print(f'Amplitude: {amplitude = } m')
print(f'Initial position: {x0 = } m')
print(f'Initial velocity: {v0 = } m/s')
print(f'Observation time: {t = } s')


User input
Rope tension: force = 10 N
Rope mass: mass = 2 Kg
Rope length: length = 1 m
Frequency: freq = 0.2 Hz
Amplitude: amplitude = 10 m
Initial position: x0 = 3 m
Initial velocity: v0 = -1 m/s
Observation time: t = 51 s


In [16]:
linear_density: float = mass/length
speed: float = np.sqrt(force/linear_density)
period: float = 1/freq
angular_freq: float = 2*np.pi*freq
wavelength: float = speed*period
k: float = 2*np.pi / wavelength
p_ave: float = np.sqrt(linear_density*force) * angular_freq**2 * amplitude**2 / 2

# Buscar phi
y0: float = np.sqrt(amplitude**2 - (v0/angular_freq)**2)
phi: float = np.pi/2 - k*x0 if y0 == 0 else np.arctan(v0/(angular_freq*y0)) - k*x0

print(f'Linear mass density: {linear_density} Kg/m')
print(f'Propagation speed: {speed} m/s')
print(f'Period: {period} s')
print(f'Angular frequency: {angular_freq} rad/s')
print(f'Wavelength: {wavelength} m')
print(f'Average power: {p_ave} J/s')
print(f'Initial phase: {phi}')

Linear mass density: 2.0 Kg/m
Propagation speed: 2.23606797749979 m/s
Period: 5.0 s
Angular frequency: 1.2566370614359172 rad/s
Wavelength: 11.180339887498949 m
Average power: 353.10570162987045 J/s
Initial phase: -1.765617235610864


In [11]:
fig, ax = plt.subplots()
ax.set_xlim(0, wavelength*2.5)
ax.set_ylim(-amplitude - .1, amplitude + .1)

line1, = ax.plot([], [], lw=2)
time_text = ax.text(0.02, 0.95, '', transform=ax.transAxes)
ax.grid()

def init():
    line1.set_data([], [])
    time_text.set_text('')
    return line1, time_text

def animate(ti):
    time_text.set_text(f'Time = {ti} s')

    x = np.linspace(0, wavelength*2.5, 10_000)
    y = amplitude * np.cos(k*x - angular_freq*ti + phi)
    line1.set_data(x, y)
    return line1,

ax.set_title('$y(x, t)$')
ax.set_xlabel('x ($m$)')
ax.set_ylabel('y ($m$)')

anim = FuncAnimation(fig, animate, init_func=init,
                     frames=t+1, interval=1./20, blit=True)
# En caso de querer guardarlo, se puede guardar como gif así:
# anim.save('rope_simulation.gif', writer='imagemagick')

plt.close() # Para quitar la gráfica que genera FuncAnimation

HTML(anim.to_jshtml())

In [13]:
fig, (ax1, ax2) = plt.subplots(nrows=2, ncols=1, figsize=(8, 7))

ax1.set_xlim(0, wavelength*2.5)
ax1.set_ylim(0, p_ave*2.1)

ax2.set_xlim(0, period*2.5)
ax2.set_ylim(0, p_ave*2.1)

line1, = ax1.plot([], [], lw=2)
line2, = ax2.plot([], [], lw=2)

time_text = ax1.text(0.02, 0.95, '', transform=ax1.transAxes)
position_text = ax2.text(0.02, 0.95, '', transform=ax2.transAxes)

ax1.grid()
ax2.grid()

def init():
    line1.set_data([], [])
    line2.set_data([], [])

    time_text.set_text('')
    position_text.set_text('')
    return line1, line2, time_text, position_text

def animate(i):
    time_text.set_text(f'Time = {i} s')
    position_text.set_text(f'Position = {i}')

    x1 = np.linspace(0, wavelength*2.5, 10_000)
    y1 = np.sqrt(linear_density * force) * angular_freq**2 * amplitude**2 * np.sin(k*x1 - angular_freq*i)**2

    x2 = np.linspace(0, period*2.5, 10_000)
    y2 = np.sqrt(linear_density * force) * angular_freq**2 * amplitude**2 * np.sin(k*i - angular_freq*x2)**2

    line2.set_data(x2, y2)
    line1.set_data(x1, y1)
    return line1, line2

fig.suptitle('$P(x, t)$')

ax1.set_xlabel('x ($m$)')
ax1.set_ylabel('E ($J$)')

ax2.set_xlabel('t ($s$)')
ax2.set_ylabel('E ($J$)')

plt.tight_layout()

anim = FuncAnimation(fig, animate, init_func=init,
                     frames=t+1, interval=1./20, blit=True)
# En caso de querer guardarlo, se puede guardar como gif así:
# anim.save('rope_simulation.gif', writer='imagemagick')

plt.close() # Para quitar la gráfica que genera FuncAnimation

HTML(anim.to_jshtml())